# Visualize tracking dataset

Load a sample from `MedicanesTrackDataset` and overlay the cyclone centre on the video tile.

Set `csv_path` and `data_root` to point to your local data.

In [1]:
import os, re
import numpy as np
import pandas as pd
from arguments import prepare_finetuning_args
from dataset.data_manager import BuildTrackingDataset, DataManager
import torch
from torch.utils.data import DataLoader
from dataset.tracking_dataset import MedicanesTrackDataset
from dataset.build_dataset import get_cyclone_center_pixel
from view_test_tiles import display_video_clip
from PIL import Image, ImageDraw


Impossibile caricare la libreria torch dynamo


In [12]:
args = prepare_finetuning_args()


# Percorsi
input_dir = "../fromgcloud"
output_dir = "../airmassRGB/supervised/" 
csv_out = "train_tracking.csv"          # CSV finale con pixel per tracking
manos_file = "medicane_data_input/more_medicanes_time_updated.csv"  #
df_tracks = pd.read_csv(manos_file, parse_dates=['time', 'start_time', 'end_time'])

bt = BuildTrackingDataset(type="supervised", args=args)
bt.prepare_data(df_tracks, input_dir, output_dir)
bt.create_tracking_csv(output_dir, csv_out)


sorted_metadata_files num :  22609
1)  ->
Con cicloni: 72
Senza cicloni: 528
600 video per il periodo (effettivo) da 2010-10-11 17:45:00 a 2010-10-13 20:00:00

2)  ->
Con cicloni: 115
Senza cicloni: 1133
1248 video per il periodo (effettivo) da 2011-11-05 05:45:00 a 2011-11-09 14:00:00

3)  ->
Con cicloni: 110
Senza cicloni: 1054
1164 video per il periodo (effettivo) da 2012-04-10 19:45:00 a 2012-04-14 21:00:00

4)  ->
Con cicloni: 64
Senza cicloni: 644
708 video per il periodo (effettivo) da 2013-11-18 10:45:00 a 2013-11-20 22:00:00

5)  ->
Con cicloni: 122
Senza cicloni: 1150
1272 video per il periodo (effettivo) da 2014-11-05 23:45:00 a 2014-11-10 10:00:00

6)  ->
Con cicloni: 105
Senza cicloni: 1047
1152 video per il periodo (effettivo) da 2014-11-29 19:45:00 a 2014-12-03 20:00:00

7)  ->
Con cicloni: 90
Senza cicloni: 870
960 video per il periodo (effettivo) da 2015-09-29 18:45:00 a 2015-10-03 03:00:00

8)  ->
Con cicloni: 96
Senza cicloni: 972
1068 video per il periodo (effettivo

In [13]:
# Costruisce DataLoader per tracking a partire dal CSV generato
dm = DataManager(is_train=False, args=args, type_t='supervised', specify_data_path=csv_out)
track_loader = dm.get_tracking_dataloader(args)
track_ds = dm.dataset


Getting TRACKING dataset (pixel coords)...
DATASET length: 2092
Creo il DistributedSampler con world_size 1 e rank 0
Sampler_train = <torch.utils.data.distributed.DistributedSampler object at 0x7ff28f206a90>
Batch_size local: 1


In [ ]:
def extract_offsets(folder_path: str):
    """Parse tile top-left corner (x, y) from folder name."""
    base = os.path.basename(folder_path.rstrip(os.sep))
    nums = [int(n) for n in re.findall(r'\d+', base)]
    if len(nums) >= 2:
        return nums[-2], nums[-1]
    return 0, 0


In [21]:
# Grab a single example
video, coords, folder = track_ds[1600]

# Undo normalization to [0, 1]
mean = torch.tensor([0.485, 0.456, 0.406]).view(3,1,1,1)
std = torch.tensor([0.229, 0.224, 0.225]).view(3,1,1,1)
video = (video * std + mean).clamp(0, 1)

# Convert to numpy [T, H, W, C]
video_np = video.permute(1, 2, 3, 0).numpy()

# coords are already tile-relative pixel coordinates (x, y)
px_tile, py_tile = coords.tolist()

# Draw the cyclone centre on each frame
frames = []
for frame in video_np:
    img = (frame * 255).astype(np.uint8)
    pil = Image.fromarray(img)
    draw = ImageDraw.Draw(pil)
    r = 2
    draw.ellipse((px_tile - r, py_tile - r, px_tile + r, py_tile + r), fill=(255, 0, 0))
    frames.append(np.asarray(pil) / 255.0)

# Display the clip
display_video_clip(frames)
